In [1]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

C:\Users\aurel\AppData\Local\Temp\ipykernel_17124\3777615979.py:1: DeprecationWarning: Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython.display
  from IPython.core.display import display, HTML


# Lab | Natural Language Processing
### SMS: SPAM or HAM

### Let's prepare the environment

In [2]:
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.feature_extraction.text import TfidfVectorizer

- Read Data for the Fraudulent Email Kaggle Challenge
- Reduce the training set to speead up development. 

In [3]:
## Read Data for the Fraudulent Email Kaggle Challenge
data = pd.read_csv("../data/kg_train.csv",encoding='latin-1')

# Reduce the training set to speed up development. 
# Modify for final system
data = data.head(1000)
print(data.shape)
data.fillna("",inplace=True)

(1000, 2)


In [4]:
data.head()

text  label
0  DEAR SIR, STRICTLY A PRIVATE BUSINESS PROPOSAL...      1
1                                           Will do.      0
2  Nora--Cheryl has emailed dozens of memos about...      0
3  Dear Sir=2FMadam=2C I know that this proposal ...      1
4                                                fyi      0

### Let's divide the training and test set into two partitions

In [5]:
# Your code
from sklearn.model_selection import train_test_split

X = data["text"]  # Features (input)
y = data["label"]  # Labels (output)

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

print(X.head(),"\n \n ")
print(y.head())

0    DEAR SIR, STRICTLY A PRIVATE BUSINESS PROPOSAL...
1                                             Will do.
2    Nora--Cheryl has emailed dozens of memos about...
3    Dear Sir=2FMadam=2C I know that this proposal ...
4                                                  fyi
Name: text, dtype: object 
 
 
0    1
1    0
2    0
3    1
4    0
Name: label, dtype: int64


## Data Preprocessing

In [6]:
import string
from nltk.corpus import stopwords
print(string.punctuation)
print(stopwords.words("english")[100:110])
from nltk.stem.snowball import SnowballStemmer
snowball = SnowballStemmer('english')

!"#$%&'()*+,-./:;<=>?@[\]^_`{|}~
['here', 'there', 'when', 'where', 'why', 'how', 'all', 'any', 'both', 'each']


## Now, we have to clean the html code removing words

- First we remove inline JavaScript/CSS
- Then we remove html comments. This has to be done before removing regular tags since comments can contain '>' characters
- Next we can remove the remaining tags

In [7]:
# Your code

import re

def clean_artfacts(X):

    cleaned_data =[]

    for sentence in X:

        # Turn into strings
        sentence = str(sentence)

        # Remove JS/CSS
        sentence = re.sub(r'<script\b[^<]*(?:(?!<\/script>)<[^<]*)*<\/script>|<style\b[^<]*(?:(?!<\/style>)<[^<]*)*<\/style>', '', sentence)

        # Remove HTML comments
        sentence = re.sub(r'<!--.*?-->', '', sentence)

        # Remove HTML tags
        sentence = re.sub(r'<[^>]+>', '', sentence)

        #Add to clean_data
        cleaned_data.append(sentence)

    return cleaned_data

X_clean=clean_artfacts(X)

X_clean

["DEAR SIR, STRICTLY A PRIVATE BUSINESS PROPOSAL I AM MIKE CHUKWU , THE MANAGER, BILLS AND EXCHANGE AT THE FOREIGN REMITTANCE DEPARTMENT OF THE ZENITH INTERNATIONAL BANK PLC. I AM WRITING THIS LETTER TO ASK FOR YOUR SUPPORT AND COOPERATION TO CARRY OUT THIS BUSINESS OPPORTUNITY IN MY DEPARTMENT. WE DISCOVERED AN ABANDONED SUM OF $15,000,000.00 (FIFTEEN MILLION UNITED STATES DOLLARS ONLY) IN AN ACCOUNT THAT BELONGS TO ONE OF OUR FOREIGN CUSTOMERS WHO DIED ALONG WITH HIS ENTIRE FAMILY OF A WIFE AND TWO CHILDREN IN NOVEMBER 1997 IN A PLANE CRASH. SINCE WE HEARD OF HIS DEATH, WE HAVE BEEN EXPECTING HIS NEXT-OF-KIN TO COME OVER AND PUT CLAIMS FOR HIS MONEY AS THE HEIR,BECAUSE WE CANNOT RELEASE THE FUND FROM HIS ACCOUNT UNLESS SOMEONE APPLIES FOR CLAIM AS THE NEXT-OF-KIN TO THE DECEASED AS INDICATED IN OUR BANKING GUIDELINES. UNFORTUNATELY, NEITHER THEIR FAMILY MEMBER NOR DISTANT RELATIVE HAS EVER APPEARED TO CLAIM THE SAID FUND. UPON THIS DISCOVERY,I AND OTHER OFFICIALS IN MY DEPARTMENT HAV

- Remove all the special characters
    
- Remove numbers
    
- Remove all single characters
 
- Remove single characters from the start

- Substitute multiple spaces with single space

- Remove prefixed 'b'

- Convert to Lowercase

In [8]:
# Your code

import re

def clean_text(text_list):

    cleaned_text =[]

    for sentence in text_list: 
        # Turn into a string
        sentence = str(sentence)

        # Remove all special characters
        sentence = re.sub(r'[^a-zA-Z\s]', ' ', sentence)  # Keep only letters and spaces
        
        # Remove numbers
        sentence = re.sub(r'\d+', ' ', sentence)
        
        # Remove all single characters
        sentence = re.sub(r'\b[a-zA-Z]\b', ' ', sentence)  # Remove isolated single letters
        
        # Remove single characters from the start
        sentence = re.sub(r'^[a-zA-Z]\s+', ' ', sentence)

        # Remove prefixed 'b' (commonly from bytes conversion)
        sentence = re.sub(r'\bb\s+', ' ', sentence)
        
        # Substitute multiple spaces with a single space
        sentence = re.sub(r'\s+', ' ', sentence).strip()
        
        # Convert to lowercase
        sentence = sentence.lower()
        
        # Append the cleaned sentence to the list
        cleaned_text.append(sentence)
    
    return cleaned_text

X_clean = clean_text(X_clean)

X_clean

['dear sir strictly private business proposal am mike chukwu the manager bills and exchange at the foreign remittance department of the zenith international bank plc am writing this letter to ask for your support and cooperation to carry out this business opportunity in my department we discovered an abandoned sum of fifteen million united states dollars only in an account that belongs to one of our foreign customers who died along with his entire family of wife and two children in november in plane crash since we heard of his death we have been expecting his next of kin to come over and put claims for his money as the heir because we cannot release the fund from his account unless someone applies for claim as the next of kin to the deceased as indicated in our banking guidelines unfortunately neither their family member nor distant relative has ever appeared to claim the said fund upon this discovery and other officials in my department have agreed to make business with you and releas

## Now let's work on removing stopwords
Remove the stopwords.

In [9]:
print(type(X_clean))  # Should be a list of strings
print(type(stopwords))  # Should be a list or set

<class 'list'>
<class 'nltk.corpus.reader.wordlist.WordListCorpusReader'>


In [10]:
# Your code

from nltk.corpus import stopwords
stopwords = set(stopwords.words("english"))


from nltk.tokenize import word_tokenize

def remove_stopwords(text, stopwords):
    cleaned_text = []  # To store cleaned sentences
    
    for sentence in text:
        # Tokenize the sentence into words
        sentence = word_tokenize(sentence)
        
        # Remove stopwords using set operations (retaining original structure)
        filtered_sentence = [word for word in sentence if word.lower() not in stopwords]
        
        # Join the filtered words back into a sentence
        cleaned_sentence = ' '.join(filtered_sentence)
        
        # Append the cleaned sentence to the result list
        cleaned_text.append(cleaned_sentence)
    
    return cleaned_text

X_clean = remove_stopwords(X_clean, stopwords)

X_clean

['dear sir strictly private business proposal mike chukwu manager bills exchange foreign remittance department zenith international bank plc writing letter ask support cooperation carry business opportunity department discovered abandoned sum fifteen million united states dollars account belongs one foreign customers died along entire family wife two children november plane crash since heard death expecting next kin come put claims money heir release fund account unless someone applies claim next kin deceased indicated banking guidelines unfortunately neither family member distant relative ever appeared claim said fund upon discovery officials department agreed make business release total amount account heir fund since one came discovered maintained account bank otherwise fund returned banks treasury unclaimed fund agreed ratio sharing stated thus foreign partner us officials department settlement local foreign expences incurred us course business upon successful completion transfer on

## Tame Your Text with Lemmatization
Break sentences into words, then use lemmatization to reduce them to their base form (e.g., "running" becomes "run"). See how this creates cleaner data for analysis!

In [11]:
# Split X_clean in words

x_split = []

for sentences in X_clean:
    sentence_split = sentences.split()
    x_split.append(sentence_split)

print(x_split)

[['dear', 'sir', 'strictly', 'private', 'business', 'proposal', 'mike', 'chukwu', 'manager', 'bills', 'exchange', 'foreign', 'remittance', 'department', 'zenith', 'international', 'bank', 'plc', 'writing', 'letter', 'ask', 'support', 'cooperation', 'carry', 'business', 'opportunity', 'department', 'discovered', 'abandoned', 'sum', 'fifteen', 'million', 'united', 'states', 'dollars', 'account', 'belongs', 'one', 'foreign', 'customers', 'died', 'along', 'entire', 'family', 'wife', 'two', 'children', 'november', 'plane', 'crash', 'since', 'heard', 'death', 'expecting', 'next', 'kin', 'come', 'put', 'claims', 'money', 'heir', 'release', 'fund', 'account', 'unless', 'someone', 'applies', 'claim', 'next', 'kin', 'deceased', 'indicated', 'banking', 'guidelines', 'unfortunately', 'neither', 'family', 'member', 'distant', 'relative', 'ever', 'appeared', 'claim', 'said', 'fund', 'upon', 'discovery', 'officials', 'department', 'agreed', 'make', 'business', 'release', 'total', 'amount', 'account',

In [12]:
#Lemmanization

from nltk.stem.wordnet import WordNetLemmatizer

# Initialize the lemmatizer
lemmatizer = WordNetLemmatizer()

x_lemma = []

for word_list in x_split:  # Assuming x_split is a list of lists of words
    lemmatized_list = []  # To store lemmatized words for the current list
    for word in word_list:
        # Lemmatize the word
        lemmatized_word = lemmatizer.lemmatize(word)
        lemmatized_list.append(lemmatized_word)  # Add to the lemmatized list
    x_lemma.append(lemmatized_list)  # Add the lemmatized list to x_lemma

print(x_lemma)


[['dear', 'sir', 'strictly', 'private', 'business', 'proposal', 'mike', 'chukwu', 'manager', 'bill', 'exchange', 'foreign', 'remittance', 'department', 'zenith', 'international', 'bank', 'plc', 'writing', 'letter', 'ask', 'support', 'cooperation', 'carry', 'business', 'opportunity', 'department', 'discovered', 'abandoned', 'sum', 'fifteen', 'million', 'united', 'state', 'dollar', 'account', 'belongs', 'one', 'foreign', 'customer', 'died', 'along', 'entire', 'family', 'wife', 'two', 'child', 'november', 'plane', 'crash', 'since', 'heard', 'death', 'expecting', 'next', 'kin', 'come', 'put', 'claim', 'money', 'heir', 'release', 'fund', 'account', 'unless', 'someone', 'applies', 'claim', 'next', 'kin', 'deceased', 'indicated', 'banking', 'guideline', 'unfortunately', 'neither', 'family', 'member', 'distant', 'relative', 'ever', 'appeared', 'claim', 'said', 'fund', 'upon', 'discovery', 'official', 'department', 'agreed', 'make', 'business', 'release', 'total', 'amount', 'account', 'heir', '

In [13]:
from nltk.stem.wordnet import WordNetLemmatizer

# Initialize the lemmatizer
lemmatizer = WordNetLemmatizer()

# Helper function to lemmatize a list of words
def lemmatize_word_list(word_list):
    return [lemmatizer.lemmatize(word) for word in word_list]


# Use list comprehension to process each word_list
x_lemma1 = [lemmatize_word_list(word_list) for word_list in x_split]

print(x_lemma1)

[['dear', 'sir', 'strictly', 'private', 'business', 'proposal', 'mike', 'chukwu', 'manager', 'bill', 'exchange', 'foreign', 'remittance', 'department', 'zenith', 'international', 'bank', 'plc', 'writing', 'letter', 'ask', 'support', 'cooperation', 'carry', 'business', 'opportunity', 'department', 'discovered', 'abandoned', 'sum', 'fifteen', 'million', 'united', 'state', 'dollar', 'account', 'belongs', 'one', 'foreign', 'customer', 'died', 'along', 'entire', 'family', 'wife', 'two', 'child', 'november', 'plane', 'crash', 'since', 'heard', 'death', 'expecting', 'next', 'kin', 'come', 'put', 'claim', 'money', 'heir', 'release', 'fund', 'account', 'unless', 'someone', 'applies', 'claim', 'next', 'kin', 'deceased', 'indicated', 'banking', 'guideline', 'unfortunately', 'neither', 'family', 'member', 'distant', 'relative', 'ever', 'appeared', 'claim', 'said', 'fund', 'upon', 'discovery', 'official', 'department', 'agreed', 'make', 'business', 'release', 'total', 'amount', 'account', 'heir', '

## Bag Of Words
Let's get the 10 top words in ham and spam messages (**EXPLORATORY DATA ANALYSIS**)

In [14]:
# Your code

from nltk import probability
import math

def bag_of_words(sentences):
    return dict([(word, True) for sentence in sentences for word in sentence])

In [16]:
# Lemma

#Bag of word lemma1

from sklearn.feature_extraction import DictVectorizer

# Generate Bag-of-Words dictionaries
Xbowl1 = bag_of_words(x_lemma1)

# # Vectorize the Bag-of-Words
# vectorizer = DictVectorizer(sparse=True)
# X_features = vectorizer.fit_transform(Xbowl1)

print(Xbowl1)

# # Check the shape of the resulting feature matrix
# print("Feature Matrix Shape:", X_features.shape)

# # View the feature names
# print("Feature Names:", vectorizer.get_feature_names_out())

{'dear': True, 'sir': True, 'strictly': True, 'private': True, 'business': True, 'proposal': True, 'mike': True, 'chukwu': True, 'manager': True, 'bill': True, 'exchange': True, 'foreign': True, 'remittance': True, 'department': True, 'zenith': True, 'international': True, 'bank': True, 'plc': True, 'writing': True, 'letter': True, 'ask': True, 'support': True, 'cooperation': True, 'carry': True, 'opportunity': True, 'discovered': True, 'abandoned': True, 'sum': True, 'fifteen': True, 'million': True, 'united': True, 'state': True, 'dollar': True, 'account': True, 'belongs': True, 'one': True, 'customer': True, 'died': True, 'along': True, 'entire': True, 'family': True, 'wife': True, 'two': True, 'child': True, 'november': True, 'plane': True, 'crash': True, 'since': True, 'heard': True, 'death': True, 'expecting': True, 'next': True, 'kin': True, 'come': True, 'put': True, 'claim': True, 'money': True, 'heir': True, 'release': True, 'fund': True, 'unless': True, 'someone': True, 'app

In [21]:


# Add the converted list to the DataFrame
data['preprocessed_text'] = x_lemma1

data.head()

text  label  \
0  DEAR SIR, STRICTLY A PRIVATE BUSINESS PROPOSAL...      1   
1                                           Will do.      0   
2  Nora--Cheryl has emailed dozens of memos about...      0   
3  Dear Sir=2FMadam=2C I know that this proposal ...      1   
4                                                fyi      0   

                                   preprocessed_text  
0  [dear, sir, strictly, private, business, propo...  
1                                                 []  
2  [nora, cheryl, emailed, dozen, memo, haiti, we...  
3  [dear, sir, fmadam, know, proposal, might, sur...  
4                                              [fyi]

## Extra features

In [23]:
# We add to the original Xframe two additional indicators (money symbols and suspicious words).

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)


money_simbol_list = "|".join(["euro","dollar","pound","€","$"])
suspicious_words = "|".join(["free","cheap","sex","money","account","bank","fund","transfer","transaction","win","deposit","password"])

X_train['money_mark'] = X_train['preprocessed_text'].str.contains(money_simbol_list)*1
X_train['suspicious_words'] = X_train['preprocessed_text'].str.contains(suspicious_words)*1
X_train['text_len'] = X_train['preprocessed_text'].apply(lambda x: len(x)) 

X_test['money_mark'] = X_test['preprocessed_text'].str.contains(money_simbol_list)*1
X_test['suspicious_words'] = X_test['preprocessed_text'].str.contains(suspicious_words)*1
X_test['text_len'] = X_test['preprocessed_text'].apply(lambda x: len(x)) 

X_train.head()

KeyError: 'preprocessed_text'

## How would work the Bag of Words with Count Vectorizer concept?

In [ ]:
# Your code

## TD-IDF

- Load the vectorizer

- Vectorize all dataset

- print the shape of the vetorized dataset

In [ ]:
# Your code

## And the Train a Classifier?

In [ ]:
# Your code

### Extra Task - Implement a SPAM/HAM classifier

https://www.kaggle.com/t/b384e34013d54d238490103bc3c360ce

The classifier can not be changed!!! It must be the MultinimialNB with default parameters!

Your task is to find the **best feature representation**.

You can work with teams of two persons (recommended).

In [ ]:
# Your code